In [1]:
from uli_init import simulate
import hoomd
import gsd
import mbuild as mb
from mbuild.formats.hoomd_simulation import create_hoomd_simulation
import hoomd.md
from hoomd.md import wall
print(mb.__path__)

['/home/chris/cme/forks/mbuild/mbuild']


In [2]:
system = simulate.System('PEEK', 1.0, 0.8, 20, 3, 'gaff', remove_hydrogens=True)

/home/chris/miniconda3/envs/uli-dev/lib/python3.7/site-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
/home/chris/cme/forks/uli-init/uli_init/simulate.py:321: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  mass = _n * np.sum(ele.element_from_symbol(p.name).mass for p in polymer.particles())
/home/chris/miniconda3/envs/uli-dev/lib/python3.7/site-packages/foyer/forcefield.py:449: UserWarning: No force field version number found in force field XML file.
  'No force field version number found in force field XML file.'
/home/chris/miniconda3/envs/uli-dev/lib/python3.7/site-packages/foyer

In [4]:
hoomd_args = f"--single-mpi --mode={'gpu'}"
sim = hoomd.context.initialize(hoomd_args)
with sim:
    objs, refs = create_hoomd_simulation(system.system_pmd, r_cut=1.2, auto_scale=True)
        # refs = distance, mass, energy
    snap = objs[0]
    hoomd_system = objs[1]
    _all = hoomd.group.all()
    hoomd.md.integrate.mode_standard(dt=0.0001)
    integrator = hoomd.md.integrate.nvt(group=_all, kT=10, tau=0.1)
    hoomd.dump.gsd("wall-squeeze.gsd", period=1e3, group=_all, phase=0, overwrite=True)
    integrator.randomize_velocities(seed=42);
 
    # Set up a wall:
    wall_origin = (snap.box.Lx/2, 0, 0)
    normal_vector = (-1, 0, 0)
    wall_origin2 = (-snap.box.Lx/2, 0, 0)
    normal_vector2 = (1, 0, 0)
    
    walls = wall.group(
                       wall.plane(origin=wall_origin, normal=normal_vector, inside = True),
                       wall.plane(origin=wall_origin2, normal=normal_vector2, inside = True)
                      )
    wall_force = wall.lj(walls, r_cut=2.5)
    wall_force.force_coeff.set(snap.particles.types, sigma=1.0, epsilon=1.0, r_extrap=0)
    
    # Set up shrink:
    reduced_target_L = system.target_L / refs[0]
    reduced_init_L = system.system_pmd.box[0] / refs[0]
    target_box = [reduced_target_L]*3
    shrink_steps = 1e5
    sim_steps = 1e5
    shrink_period = 10
    x_variant = hoomd.variant.linear_interp([(0, reduced_init_L),
                                             (shrink_steps, target_box[0]*10)])
    y_variant = hoomd.variant.linear_interp([(0, reduced_init_L),
                                             (shrink_steps, target_box[1]*10)])
    z_variant = hoomd.variant.linear_interp([(0, reduced_init_L),
                                             (shrink_steps, target_box[2]*10)])
    box_updater = hoomd.update.box_resize(Lx = x_variant, Ly = y_variant, Lz = z_variant,
                                         period = shrink_period)
    
    hoomd.util.quiet_status()
    step = 0
    while step < shrink_steps:
        hoomd.run_upto(step + shrink_period)
        snap = hoomd_system.take_snapshot()
        walls.del_plane([0,1])
        walls.add_plane((snap.box.Lx/2, 0, 0), (-1, 0, 0))
        walls.add_plane((-snap.box.Lx/2, 0, 0), (1, 0, 0))
       
        step += shrink_period
        
    box_updater.disable()
    hoomd.run(sim_steps)
        

/home/chris/miniconda3/envs/uli-dev/lib/python3.7/site-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


notice(2): Group "all" created containing 1320 particles
notice(2): -- Neighborlist exclusion statistics -- :
notice(2): Particles with 3 exclusions             : 80
notice(2): Particles with 4 exclusions             : 100
notice(2): Particles with 5 exclusions             : 620
notice(2): Particles with 6 exclusions             : 340
notice(2): Particles with 7 exclusions             : 180
notice(2): Neighbors included by diameter          : no
notice(2): Neighbors excluded when in the same body: no
Processing LJ and QQ
notice(2): Group "charged" created containing 0 particles
No charged groups found, ignoring electrostatics
Processing 1-4 interactions, adjusting neighborlist exclusions
Processing harmonic bonds
Processing harmonic angles
Processing periodic torsions
HOOMD SimulationContext updated from ParmEd Structure
** starting run **
Time 00:00:00 | Step 10 / 10 | TPS 40.0546 | ETA 00:00:00
Average TPS: 39.9222
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates 

n_neigh_min: 3 / n_neigh_max: 22 / n_neigh_avg: 9.14545
shortest rebuild period: 100
-- Cell list stats:
Dimension: 30, 30, 30
n_min    : 0 / n_max: 12 / n_avg: 0.0488889
** run complete **
** starting run **
Time 00:00:00 | Step 210 / 210 | TPS 723.694 | ETA 00:00:00
Average TPS: 656.383
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 3 / n_neigh_max: 22 / n_neigh_avg: 9.1197
shortest rebuild period: 100
-- Cell list stats:
Dimension: 30, 30, 30
n_min    : 0 / n_max: 12 / n_avg: 0.0488889
** run complete **
** starting run **
Time 00:00:00 | Step 220 / 220 | TPS 922.68 | ETA 00:00:00
Average TPS: 819.605
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 3 / n_neigh_max: 22 / n_neigh_avg: 9.09697
shortest rebuild period: 100
-- Cell list stats:
Dimension: 30, 30, 30
n_min    : 0 / n_max: 12 / n_avg: 0.0488889
** run complete **
** starting run **
Time 00:00:00 | Step 230 / 230 

Time 00:00:01 | Step 420 / 420 | TPS 872.981 | ETA 00:00:00
Average TPS: 833.611
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 3 / n_neigh_max: 23 / n_neigh_avg: 8.89091
shortest rebuild period: 100
-- Cell list stats:
Dimension: 30, 30, 30
n_min    : 0 / n_max: 12 / n_avg: 0.0488889
** run complete **
** starting run **
Time 00:00:01 | Step 430 / 430 | TPS 615.385 | ETA 00:00:00
Average TPS: 595.983
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 3 / n_neigh_max: 23 / n_neigh_avg: 8.89545
shortest rebuild period: 100
-- Cell list stats:
Dimension: 30, 30, 30
n_min    : 0 / n_max: 12 / n_avg: 0.0488889
** run complete **
** starting run **
Time 00:00:01 | Step 440 / 440 | TPS 960.799 | ETA 00:00:00
Average TPS: 927.214
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 3 / n_neigh_max: 23 / n_neigh_avg: 8.89394
shortest r

shortest rebuild period: 100
-- Cell list stats:
Dimension: 30, 30, 30
n_min    : 0 / n_max: 11 / n_avg: 0.0488889
** run complete **
** starting run **
Time 00:00:01 | Step 640 / 640 | TPS 714.49 | ETA 00:00:00
Average TPS: 689.132
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 3 / n_neigh_max: 19 / n_neigh_avg: 8.87121
shortest rebuild period: 100
-- Cell list stats:
Dimension: 30, 30, 30
n_min    : 0 / n_max: 11 / n_avg: 0.0488889
** run complete **
** starting run **
Time 00:00:01 | Step 650 / 650 | TPS 770.832 | ETA 00:00:00
Average TPS: 742.501
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 3 / n_neigh_max: 19 / n_neigh_avg: 8.87424
shortest rebuild period: 100
-- Cell list stats:
Dimension: 30, 30, 30
n_min    : 0 / n_max: 11 / n_avg: 0.0488889
** run complete **
** starting run **
Time 00:00:01 | Step 660 / 660 | TPS 968.898 | ETA 00:00:00
Average TPS: 777.907
-----

...

shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 17 / n_avg: 6.11111
** run complete **
** starting run **
Time 00:02:06 | Step 99090 / 99090 | TPS 3749.53 | ETA 00:00:00
Average TPS: 3369.27
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 5 / n_neigh_max: 42 / n_neigh_avg: 20.3394
shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 17 / n_avg: 6.11111
** run complete **
** starting run **
Time 00:02:06 | Step 99100 / 99100 | TPS 3946.33 | ETA 00:00:00
Average TPS: 3544.84
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 5 / n_neigh_max: 41 / n_neigh_avg: 20.3606
shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 17 / n_avg: 6.11111
** run complete **
** starting run **
Time 00:02:06 | Step 99110 / 99110 | TPS 4084.97 | ETA 00:00:00
Average TPS: 3623.19
-------

---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 5 / n_neigh_max: 41 / n_neigh_avg: 20.7576
shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 16 / n_avg: 6.11111
** run complete **
** starting run **
Time 00:02:06 | Step 99310 / 99310 | TPS 3287.31 | ETA 00:00:00
Average TPS: 2982.4
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 6 / n_neigh_max: 41 / n_neigh_avg: 20.7773
shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 16 / n_avg: 6.11111
** run complete **
** starting run **
Time 00:02:06 | Step 99320 / 99320 | TPS 3302.51 | ETA 00:00:00
Average TPS: 2979.74
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 5 / n_neigh_max: 41 / n_neigh_avg: 20.7955
shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 16 /

** run complete **
** starting run **
Time 00:02:06 | Step 99520 / 99520 | TPS 4070 | ETA 00:00:00
Average TPS: 3625.82
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 5 / n_neigh_max: 43 / n_neigh_avg: 21.2879
shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 15 / n_avg: 6.11111
** run complete **
** starting run **
Time 00:02:06 | Step 99530 / 99530 | TPS 4852.01 | ETA 00:00:00
Average TPS: 4323.39
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 5 / n_neigh_max: 43 / n_neigh_avg: 21.2864
shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 15 / n_avg: 6.11111
** run complete **
** starting run **
Time 00:02:06 | Step 99540 / 99540 | TPS 3501.4 | ETA 00:00:00
Average TPS: 2675.23
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 4 / n_neigh_max: 

shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 14 / n_avg: 6.11111
** run complete **
** starting run **
Time 00:02:06 | Step 99740 / 99740 | TPS 4154.55 | ETA 00:00:00
Average TPS: 3619.25
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 5 / n_neigh_max: 43 / n_neigh_avg: 21.6364
shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 14 / n_avg: 6.11111
** run complete **
** starting run **
Time 00:02:06 | Step 99750 / 99750 | TPS 3011.14 | ETA 00:00:00
Average TPS: 2701.24
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 5 / n_neigh_max: 43 / n_neigh_avg: 21.6379
shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 14 / n_avg: 6.11111
** run complete **
** starting run **
Time 00:02:06 | Step 99760 / 99760 | TPS 3084.52 | ETA 00:00:00
Average TPS: 2836.07
-------

---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 3 / n_neigh_max: 42 / n_neigh_avg: 22.1288
shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 14 / n_avg: 6.11111
** run complete **
** starting run **
Time 00:02:06 | Step 99960 / 99960 | TPS 3202.05 | ETA 00:00:00
Average TPS: 2902.76
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 3 / n_neigh_max: 41 / n_neigh_avg: 22.1545
shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 14 / n_avg: 6.11111
** run complete **
** starting run **
Time 00:02:06 | Step 99970 / 99970 | TPS 4498.43 | ETA 00:00:00
Average TPS: 3985.65
---------
-- Neighborlist stats:
0 normal updates / 1 forced updates / 0 dangerous updates
n_neigh_min: 3 / n_neigh_max: 41 / n_neigh_avg: 22.1773
shortest rebuild period: 100
-- Cell list stats:
Dimension: 6, 6, 6
n_min    : 0 / n_max: 13 